In [ ]:
import cadquery as cq

In [239]:
from jupyter_cadquery.occ import show, Part, Assembly
from cadquery.occ_impl.shapes import downcast

In [240]:
import html

def rgb(assy):
    def b(x):
        return int(255*x)
    
    if assy.color is None:
        return "#aaa"
    rgb = assy.color.wrapped.GetRGB()
    return "#%02x%02x%02x" % (b(rgb.Red()), b(rgb.Green()), b(rgb.Blue()))

def convert(assy, loc=None):
    loc = assy.loc if loc is None else loc * assy.loc
    color = rgb(assy)
    parent = [Part(shape.located(loc).wrapped, "%s_%d" % (assy.name, i), color=color) for i, shape in enumerate(assy.shapes)]
    children = [convert(c, loc) for c in assy.children]
    return Assembly(parent + children, assy.name)

colors = [
    "#e41a1c","#377eb8","#4daf4a","#984ea3","#ff7f00","#ffff33","#a65628","#f781bf","#999999",
    "#8dd3c7","#ffffb3","#bebada","#fb8072","#80b1d3","#fdb462","#b3de69","#fccde5","#d9d9d9",
]

def show_constraints(assy, *qs):
    constraints = []
    objects = []
    cache = {}
    for i, q1q2 in enumerate(qs):
        parts = []
        for q in q1q2[:2]:
            name, kind, arg = q.split("@")
            if name in cache:
                obj = cache[name]["obj"]
                loc = cache[name]["loc"]
            else:
                obj = assy.objects[name].obj
                loc = assy.objects[name].loc
                parent = assy.objects[name].parent
            
                while parent is not None:
                    loc = parent.loc * loc
                    parent = parent.parent
                cache[name] =  {"obj": obj, "loc": loc}
            
                objects.append(
                    Part(obj.objects[0].located(loc).wrapped, name=name, show_faces=False)
                )
            parts.append(
                Part(downcast(assy._query(q)[1].wrapped.Located(loc.wrapped)), name=html.escape(q), color=colors[i%len(colors)])
            )
        constraints.append(Assembly(parts, "%s_%d" % (q1q2[2], i)))
    show(Assembly([Assembly(objects, "objects")] + constraints), axes=True, axes0=True)

In [194]:
def L(x,y,z):
    return cq.Location(cq.Vector(x, y, z))
def C(c):
    return cq.Color(c)

In [195]:
def create():
    b1 = cq.Workplane().box(1, 1, 2).faces('>Z').edges('>X').chamfer(0.4)
    b2 = cq.Workplane().box(.1, 2, 1).faces('>Z').edges('>Y').chamfer(0.1)
    b3 = cq.Workplane().box(2, .1, .5).faces('>Z').edges('>X').chamfer(0.1)
    b4 = cq.Workplane().box(1, 1, .2).faces('>Y').edges('>X').chamfer(0.1)

    assy = cq.Assembly(b1, loc=L(1, 1, 0), name="TOP")
    assy2 = cq.Assembly(b2, name="SECOND")
    assy3 = cq.Assembly(b3, name="THIRD", color=C('orange'))

    assy.add(assy2, color=C("green"))
    assy.add(assy3)
    assy.add(b4, name="4th",color=C("blue1"))
    return assy

In [303]:
assy = create()
cs = [
    ("TOP@faces@>(1,0,1)", "THIRD@faces@>Z", "Plane"), 
    ("TOP@faces@<Y", "SECOND@faces@<Y", "Axis"),
    ("THIRD@faces@<X", "SECOND@faces@>X", "Plane"),
    ("SECOND@faces@>Z", "THIRD@faces@<Z", "Axis"),
    ("4th@faces@>Z", "SECOND@faces@<Z", "Plane"),
    ("4th@faces@>Y", "TOP@faces@<Y", "Axis"),    
]
show_constraints(assy, *cs)

In [304]:
for c in cs:
    assy.constrain(*c)

assy.solve()
#show(convert(assy))
show_constraints(assy, *cs)

b'CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL'


In [305]:
assy = create()
cs = []
cs.append(("TOP@faces@>(1,0,1)", "THIRD@faces@>Z", "Axis"))
cs.append(("TOP@faces@>Y", "THIRD@faces@<Y", "Axis"))
cs.append(("TOP@vertices@>(1,1,2)", "THIRD@vertices@>(1,1,2)", "Point"))

for c in cs:
    assy.constrain(*c)

show_constraints(assy, *cs)

In [306]:
assy.solve()
show_constraints(assy, *cs)

b'CONVERGENCE: NORM_OF_PROJECTED_GRADIENT_<=_PGTOL'


In [296]:
show(convert(assy))

In [ ]:
assy.constrain("TOP@faces@>(1,0,1)", "THIRD@faces@>Z", "Plane")
assy.constrain("TOP@faces@<Y", "SECOND@faces@<Y", "Axis")
assy.constrain("THIRD@faces@<X", "SECOND@faces@>X", "Plane")
assy.constrain("SECOND@faces@>Z", "THIRD@faces@<Z", "Axis")
assy.constrain("4th@faces@>Z", "SECOND@faces@<Z", "Plane")
assy.constrain("4th@faces@>Y", "TOP@faces@<Y", "Axis")
assy.solve()

In [ ]:
show(convert(assy))

In [81]:
import cadquery as cq
cq.occ_impl.shapes.Shape.clean = lambda x: x
from jupyter_cadquery.cadquery import show as showcq

In [93]:
def ring(inner_radius, outer_radius, width):
    ring = (cq.Workplane('XY', origin=(0, 0, -width / 2))
        .circle(outer_radius).circle(inner_radius)
        .extrude(width)
    )
    return ring

tol = 0.02
ball_diam = 5
r1, r2, r3, r4 = 4, 6, 8, 10
r5 = (r3 + r2) / 2
inner_ring = ring(r1, r2, ball_diam)
outer_ring = ring(r3, r4, ball_diam)
torus = cq.CQ(cq.Solid.makeTorus(r5, ball_diam / 2 + tol))
ball = cq.Workplane('XY').sphere(ball_diam / 2)
showcq(ball, inner_ring.cut(torus), outer_ring.cut(torus))